## Set the chum URI here:

In [ ]:
chum_uri = 'chum://20190830T014725-kitt_09@1567129707-1567129720'

#### Preparing the notebook

In [ ]:
from IPython.core.display import display, HTML, Javascript
display(HTML("<style>.container { width:95% !important; }</style>"))

from bokeh.io import output_notebook, reset_output
reset_output()
output_notebook()

## Setting up the view

Create a set of widgets and a nested list layout to organize the widgets. Pass the layout to the `SearchResultsPlotter` widget and sync all plotters' `notebook_handle`s.

In [ ]:
from vis.jupyter_notebooks.plotters import MultiCostPlotter, SearchResultsPlotter
from vis.jupyter_notebooks.plotters import XRayVideo
from vis.jupyter_notebooks.plotters import move_slider_to_toolbar

# Instantiating the widgets
cp = MultiCostPlotter(['/[CostResults]'], cap=200)

# Currently you need to find the `video_uri` manually from Argus
# `start_time` can be extracted from the video_uri
video_uri = 'https://zoox-argus.s3.us-west-1.amazonaws.com/20190830T014725-kitt_09/kitt_09-1567129645'
start_time = 1567129645
xray = XRayVideo(video_uri, start_time)

# Setting up the layout:
# Request any plots of interest over different rollouts from SearchResults proto.
# e.g. (x, y), (t, vx), (s, ax), etc.
# Combine it with other widgets/views.
view_layout = [
#     [('x', 'y'), ('t', 'vx'), ('s', 'ax')],
    [('x', 'y'), ('t', 'vx')],
    [xray, cp.layout],
#     [xray, cp.figures, cp.side_panel],
]

# Pass the layout to the last widget and visualize.
# Also connect the cost plotter by passing it as an argument.
srp = SearchResultsPlotter(view_layout, pool_cap=200, max_depth=2, cost_plotter=cp)
srp.redraw() # This would be equivalent to srp.notebook_handle = show(srp.layout, notebook_handle=True)

## Connect to the data


In [ ]:
from vehicle.common.proto.decision_debug_pb2 import Decision as DecisionDebug
from data.tools.chum_interactor import ChumInteractor
from data.tools.chum_interactor.interactor import setup_interactors

# Loading the msgs for global cost plot
cp.global_result_map_from_chum(chum_uri)

# Setting up the interactors and connect it to `timestamp`
TOPIC_DECISION_DEBUG = '/planner/decision/debug'
interactors = setup_interactors(chum_uri, (TOPIC_DECISION_DEBUG, DecisionDebug))
interactors[TOPIC_DECISION_DEBUG].select_one('timestamp').select_field('search_results').cb(srp.update_all).display()

move_slider_to_toolbar()